# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model loaded [TRPO]

Installing required packages and dependencies

In [1]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [2]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

Cloning into 'RL_VPP_Thesis'...
remote: Enumerating objects: 393, done.
remote: Total 393 (delta 0), reused 0 (delta 0), pack-reused 393
Receiving objects: 100% (393/393), 147.26 MiB | 25.30 MiB/s, done.
Resolving deltas: 100% (149/149), done.
Checking out files: 100% (108/108), done.
/content/RL_VPP_Thesis
Agent_trainer_notebooks/          README.md             VPP_environment.py
data/                             Simulator_notebooks/  VPP_simulator.ipynb
Hyperparameters_sweep_notebooks/  trained_models/       wandb/


In [3]:
import yaml
import numpy as np
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import TRPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')
wandb, version 0.13.4


In [4]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [5]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
#case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f7e1ade1450>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 20
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 20, 'EVs_n_max': 1044, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [6]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [7]:
env.plot_ELVIS_data()

In [8]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21667.2 , over-consume=kWh  39413.52 , under-consume=kWh  17746.32 , Total_cost=€  949.9 , overcost=€  1442.84 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [9]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [10]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [11]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [12]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [13]:
env.plot_VPP_Elvis_comparison()

In [14]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [15]:
env.plot_rewards_stats()

In [16]:
env.plot_EVs_kpi()

In [17]:
env.plot_actions_kpi()

In [18]:
env.plot_load_kpi()

In [19]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [20]:
## Wandb login to load models
#In Colab, uncomment below:
%env "WANDB_DISABLE_CODE" True
%env "WANDB_NOTEBOOK_NAME" "Simulator_notebooks/TRPO_VPP_simulator.ipynb"
os.environ['WANDB_NOTEBOOK_NAME'] = 'Simulator_notebooks/TRPO_VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

env: "WANDB_DISABLE_CODE"=True
env: "WANDB_NOTEBOOK_NAME"="Simulator_notebooks/TRPO_VPP_simulator.ipynb"


In [21]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/TRPO_models/model_TRPO_"

model_id = "2ydih28d"
model = TRPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

## Testing dataset VPP Simulation using the loaded trained model

In [22]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21857.84 , over-consume=kWh  38766.08 , under-consume=kWh  16908.24 , Total_cost=€  857.17 , overcost=€  1351.09 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -5052.71 , over-consume=KWh  1598.2 , under-consume=KWh  6650.91 , Total_cost=€  -120.18 , Overcost=€  54.78 
 EV_INFO: Av.EV_energy_leaving=kWh  65.67 , Std.EV_energy_leaving=kWh  27.03 , EV_departures =  1043 , EV_queue_left =  0
SCORE:  Cumulative_reward= 360092.8 - Step_rewars (load_t= 335177.45, EVs_energy_t= 2123.27)
 - Final_rewards (EVs_energy= 14987.66, Overconsume= -866.4, Underconsume= -3625.37, Overcost= 12296.19)
Episode:1 Score:360092.80119580723


In [23]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [24]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  54.502697  45.799267   0.000000   0.000000   
2022-01-01 00:15:00  54.752697  44.728920   0.000000   0.000000   
2022-01-01 00:30:00  55.002697  44.023575   0.000000   0.000000   
2022-01-01 00:45:00  55.252697  43.050900   0.000000   0.000000   
2022-01-01 01:00:00  55.502697  42.424023   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  88.439835   0.000000  99.989998  99.989998   
2022-06-06 05:00:00  89.455070   0.000000  99.989998  99.989998   
2022-06-06 05:15:00  90.473083   0.000000  99.989998  99.989998   
2022-06-06 05:30:00  91.530663   0.000000  99.989998  99.989998   
2022-06-06 05:45:00  92.500587   0.000000  99.989998  99.989998   

                                    EVs_id       actions  \
time                                                       
2022-01-01 00:00:00           [0, 0, 0, 0]  [1, 2, 2, 0]   
2022-01-01 00:15:00     [3128, 3129, 0, 0]  [1, 2, 2, 0]   
2022-01-01 00:30:00     [3128, 3129, 0, 0]  [1, 2, 2, 0]   
2022-01-01 00:45:00     [3128, 3129, 0, 0]  [1, 2, 2, 0]   
2022-01-01 01:00:00     [3128, 3129, 0, 0]  [1, 2, 2, 0]   
...                                    ...           ...   
2022-06-06 04:45:00  [3559, 0, 3557, 3558]  [1, 0, 1, 1]   
2022-06-06 05:00:00  [3559, 0, 3557, 3558]  [1, 0, 1, 1]   
2022-06-06 05:15:00  [3559, 0, 3557, 3558]  [1, 0, 1, 1]   
2022-06-06 05:30:00  [3559, 0, 3557, 3558]  [1, 0, 1, 1]   
2022-06-06 05:45:00  [3559, 0, 3557, 3558]  [1, 0, 1, 1]   

                                      mask_truth          load  load_reward  \
time                                                                          
2022-01-01 00:00:00  [False, False, False, True]  2.092229e+00    15.000000   
2022-01-01 00:15:00   [False, True, False, True]  4.440892e-16    15.000000   
2022-01-01 00:30:00   [False, True, False, True]  0.000000e+00    15.000000   
2022-01-01 00:45:00   [False, True, False, True]  0.000000e+00    15.000000   
2022-01-01 01:00:00   [False, True, False, True] -2.220446e-16    15.000000   
...                                          ...           ...          ...   
2022-06-06 04:45:00   [True, True, False, False] -5.425678e+00    -8.747146   
2022-06-06 05:00:00   [True, True, False, False] -8.121861e+00    -8.767328   
2022-06-06 05:15:00   [True, True, False, False] -8.144061e+00    -9.055115   
2022-06-06 05:30:00   [True, True, False, False] -8.460626e+00    -8.417633   
2022-06-06 05:45:00   [True, True, False, False] -7.759397e+00    -8.773481   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  15.000000  
2022-01-01 00:15:00        0.0  15.000000  
2022-01-01 00:30:00        0.0  15.000000  
2022-01-01 00:45:00        0.0  15.000000  
2022-01-01 01:00:00        0.0  15.000000  
...                        ...        ...  
2022-06-06 04:45:00        0.0  -8.747146  
2022-06-06 05:00:00        0.0  -8.767328  
2022-06-06 05:15:00        0.0  -9.055115  
2022-06-06 05:30:00        0.0  -8.417633  
2022-06-06 05:45:00        0.0  -8.773481  

[15000 rows x 11 columns]

In [25]:
#env.plot_Elvis_results()

In [26]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [27]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [28]:
env.plot_VPP_Elvis_comparison()

In [29]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [30]:
env.plot_rewards_stats()

In [31]:
env.plot_EVs_kpi()

In [32]:
env.plot_load_kpi()

In [33]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [34]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 4173, Arrival time: 2022-01-01 12:45:00, Parking_time: 24, Leaving_time: 2022-01-02 12:45:00, SOC: 0.5429452457064987, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 5215, Arrival time: 2022-12-31 11:15:00, Parking_time: 24, Leaving_time: 2023-01-01 11:15:00, SOC: 0.3654117462026696, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  13186.85 , over-consume=kWh  34353.23 , under-consume=kWh  21166.38 , Total_cost=€  640.36 , overcost=€  1505.17 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  80.89


In [35]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [36]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = TRPO.load(RecurrentPPO_path + model_id, env=env)

In [37]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  12741.52 , over-consume=kWh  34101.29 , under-consume=kWh  21359.76 , Total_cost=€  628.35 , overcost=€  1500.48 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  80.89
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -7415.2 , over-consume=KWh  1400.35 , under-consume=KWh  8815.55 , Total_cost=€  -268.92 , Overcost=€  60.17 
 EV_INFO: Av.EV_energy_leaving=kWh  71.58 , Std.EV_energy_leaving=kWh  26.12 , EV_departures =  1038 , EV_queue_left =  1
SCORE:  Cumulative_reward= 352654.84 - Step_rewars (load_t= 306182.47, EVs_energy_t= 21004.51)
 - Final_rewards (EVs_energy= 17934.6, Overconsume= -859.77, Underconsume= -3988.45, Overcost= 12381.49)
Episode:1 Score:352654.84215745097


In [38]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [39]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  68.700905  62.899773   0.000000  88.003677   
2022-06-06 05:00:00  69.881966  64.080833   0.000000  89.184738   
2022-06-06 05:15:00  71.112198  65.311066  36.232586  90.414970   
2022-06-06 05:30:00  72.356819  66.555687  35.982586  91.659592   
2022-06-06 05:45:00  73.573257  67.772125  35.732586  92.876030   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [1, 0, 2, 1]   
2022-01-01 00:15:00              [0, 0, 0, 0]  [1, 0, 2, 1]   
2022-01-01 00:30:00              [0, 0, 0, 0]  [1, 0, 2, 1]   
2022-01-01 00:45:00              [0, 0, 0, 0]  [1, 0, 2, 1]   
2022-01-01 01:00:00              [0, 0, 0, 0]  [1, 0, 2, 1]   
...                                       ...           ...   
2022-06-06 04:45:00     [6679, 6680, 0, 6678]  [1, 1, 0, 1]   
2022-06-06 05:00:00     [6679, 6680, 0, 6678]  [1, 1, 0, 1]   
2022-06-06 05:15:00  [6679, 6680, 6681, 6678]  [1, 1, 2, 1]   
2022-06-06 05:30:00  [6679, 6680, 6681, 6678]  [1, 1, 2, 1]   
2022-06-06 05:45:00  [6679, 6680, 6681, 6678]  [1, 1, 2, 1]   

                                      mask_truth          load  load_reward  \
time                                                                          
2022-01-01 00:00:00  [False, True, False, False] -4.415466e+00    -4.352027   
2022-01-01 00:15:00  [False, True, False, False] -3.611216e+00    -5.163792   
2022-01-01 00:30:00  [False, True, False, False] -4.180171e+00    -2.955950   
2022-01-01 00:45:00  [False, True, False, False] -2.773570e+00    -4.758928   
2022-01-01 01:00:00  [False, True, False, False] -3.855357e+00    -3.764772   
...                                          ...           ...          ...   
2022-06-06 04:45:00     [True, True, True, True]  0.000000e+00    15.000000   
2022-06-06 05:00:00     [True, True, True, True]  0.000000e+00    15.000000   
2022-06-06 05:15:00    [True, True, False, True] -1.776357e-15    15.000000   
2022-06-06 05:30:00   [True, True, False, False]  0.000000e+00    15.000000   
2022-06-06 05:45:00   [True, True, False, False]  0.000000e+00    15.000000   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  -4.352027  
2022-01-01 00:15:00        0.0  -5.163792  
2022-01-01 00:30:00        0.0  -2.955950  
2022-01-01 00:45:00        0.0  -4.758928  
2022-01-01 01:00:00        0.0  -3.764772  
...                        ...        ...  
2022-06-06 04:45:00        0.0  15.000000  
2022-06-06 05:00:00        0.0  15.000000  
2022-06-06 05:15:00        0.0  15.000000  
2022-06-06 05:30:00        0.0  15.000000  
2022-06-06 05:45:00        0.0  15.000000  

[15000 rows x 11 columns]

In [40]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [41]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [42]:
env.plot_VPP_Elvis_comparison()

In [43]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [44]:
env.plot_rewards_stats()

In [45]:
env.plot_EVs_kpi()

In [46]:
env.plot_load_kpi()

In [47]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [48]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 7302, Arrival time: 2022-01-01 00:00:00, Parking_time: 24, Leaving_time: 2022-01-02 00:00:00, SOC: 0.634963688998057, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 8344, Arrival time: 2022-12-31 19:00:00, Parking_time: 24, Leaving_time: 2023-01-01 19:00:00, SOC: 0.5702403524116723, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  7918.73 , over-consume=kWh  31305.27 , under-consume=kWh  23386.54 , Total_cost=€  445.7 , overcost=€  1307.28 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  84.2


In [49]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [50]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = TRPO.load(RecurrentPPO_path + model_id, env=env)

In [51]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  9379.9 , over-consume=kWh  32327.99 , under-consume=kWh  22948.09 , Total_cost=€  510.24 , overcost=€  1349.67 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  84.2
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -9132.45 , over-consume=KWh  1114.79 , under-consume=KWh  10247.25 , Total_cost=€  -315.68 , Overcost=€  46.5 
 EV_INFO: Av.EV_energy_leaving=kWh  73.6 , Std.EV_energy_leaving=kWh  25.66 , EV_departures =  1041 , EV_queue_left =  0
SCORE:  Cumulative_reward= 357757.82 - Step_rewars (load_t= 305615.86, EVs_energy_t= 26308.0)
 - Final_rewards (EVs_energy= 17594.36, Overconsume= -591.18, Underconsume= -4622.63, Overcost= 13453.4)
Episode:1 Score:357757.81852518115


In [52]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [53]:
VPP_table.head(15000)

0          1    2    3              EVs_id  \
time                                                                      
2022-01-01 00:00:00   0.000000   0.000000  0.0  0.0        [0, 0, 0, 0]   
2022-01-01 00:15:00   0.000000   0.000000  0.0  0.0        [0, 0, 0, 0]   
2022-01-01 00:30:00   0.000000   0.000000  0.0  0.0        [0, 0, 0, 0]   
2022-01-01 00:45:00   0.000000   0.000000  0.0  0.0        [0, 0, 0, 0]   
2022-01-01 01:00:00   0.000000   0.000000  0.0  0.0        [0, 0, 0, 0]   
...                        ...        ...  ...  ...                 ...   
2022-06-06 04:45:00  71.975037  93.787331  0.0  0.0  [9824, 9823, 0, 0]   
2022-06-06 05:00:00  73.265556  95.077850  0.0  0.0  [9824, 9823, 0, 0]   
2022-06-06 05:15:00  74.498352  96.310646  0.0  0.0  [9824, 9823, 0, 0]   
2022-06-06 05:30:00  75.597153  97.409447  0.0  0.0  [9824, 9823, 0, 0]   
2022-06-06 05:45:00  76.681053  98.493347  0.0  0.0  [9824, 9823, 0, 0]   

                          actions                   mask_truth      load  \
time                                                                       
2022-01-01 00:00:00  [1, 0, 2, 1]  [False, True, False, False] -3.419696   
2022-01-01 00:15:00  [1, 0, 2, 1]  [False, True, False, False] -3.866481   
2022-01-01 00:30:00  [1, 0, 2, 1]  [False, True, False, False] -2.855728   
2022-01-01 00:45:00  [1, 0, 2, 1]  [False, True, False, False] -3.415430   
2022-01-01 01:00:00  [1, 0, 2, 1]  [False, True, False, False] -5.542320   
...                           ...                          ...       ...   
2022-06-06 04:45:00  [1, 1, 2, 0]   [True, False, False, True]  0.000000   
2022-06-06 05:00:00  [1, 1, 2, 0]   [True, False, False, True]  0.000000   
2022-06-06 05:15:00  [1, 1, 2, 0]   [True, False, False, True]  0.000000   
2022-06-06 05:30:00  [1, 1, 2, 0]   [True, False, False, True]  0.000000   
2022-06-06 05:45:00  [1, 1, 2, 0]   [True, False, False, True]  0.000000   

                     load_reward  EV_reward    rewards  
time                                                    
2022-01-01 00:00:00    -4.777469        0.0  -4.777469  
2022-01-01 00:15:00    -3.092879        0.0  -3.092879  
2022-01-01 00:30:00    -4.025716        0.0  -4.025716  
2022-01-01 00:45:00    -6.402109        0.0  -6.402109  
2022-01-01 01:00:00    -6.390637        0.0  -6.390637  
...                          ...        ...        ...  
2022-06-06 04:45:00    15.000000        0.0  15.000000  
2022-06-06 05:00:00    15.000000        0.0  15.000000  
2022-06-06 05:15:00    15.000000        0.0  15.000000  
2022-06-06 05:30:00    15.000000        0.0  15.000000  
2022-06-06 05:45:00    15.000000        0.0  15.000000  

[15000 rows x 11 columns]

In [54]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [55]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [56]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

In [ ]:
#env.close()